In [1]:
!sudo add-apt-repository -y ppa:jonathonf/ffmpeg-4
!sudo apt update
!sudo apt install -y ffmpeg
!sudo apt-get install git-lfs

!sudo apt-get install git-lfs

#python3 -m venv hf_env
#source hf_env/bin/activate
#echo "source ~/hf_env/bin/activate" >> ~/.bashrc

!git clone https://github.com/huggingface/community-events.git
!pip install -r community-events/whisper-fine-tuning-event/requirements.txt

!git config --global credential.helper store
#!huggingface-cli login


Get:1 https://nvidia.github.io/libnvidia-container/stable/ubuntu18.04/amd64  InRelease [1484 B]
Get:2 https://download.docker.com/linux/ubuntu focal InRelease [57.7 kB]       
Hit:3 https://nvidia.github.io/nvidia-container-runtime/stable/ubuntu18.04/amd64  InRelease
Get:4 http://security.ubuntu.com/ubuntu focal-security InRelease [114 kB]      
Get:5 https://packages.microsoft.com/repos/azure-cli focal InRelease [10.4 kB] 
Get:6 https://packages.cloud.google.com/apt cloud-sdk InRelease [6751 B]       
Hit:7 http://archive.ubuntu.com/ubuntu focal InRelease                         
Get:8 https://download.docker.com/linux/ubuntu focal/stable amd64 Packages [22.2 kB]
Get:9 http://archive.ubuntu.com/ubuntu focal-updates InRelease [114 kB]        
Ign:10 http://ppa.launchpad.net/jonathonf/ffmpeg-4/ubuntu focal InRelease      
Get:11 http://archive.ubuntu.com/ubuntu focal-backports InRelease [108 kB]     
Get:12 https://packages.microsoft.com/repos/azure-cli focal/main amd64 Packages [9926 B

In [2]:
!nvidia-smi

Sun Dec 18 15:29:23 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 515.65.01    Driver Version: 515.65.01    CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  On   | 00000000:06:00.0 Off |                    0 |
| N/A   33C    P0    46W / 400W |      0MiB / 40960MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!python -c "import torch; print(torch.cuda.is_available())"

True


In [3]:
import torch
from transformers import WhisperFeatureExtractor, WhisperForConditionalGeneration
from datasets import load_dataset

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-tiny")
feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-tiny")

common_voice = load_dataset("common_voice", "en", split="validation", streaming=True)

inputs = feature_extractor(next(iter(common_voice))["audio"]["array"], sampling_rate=16000, return_tensors="pt")
input_features = inputs.input_features

decoder_input_ids = torch.tensor([[1, 1]]) * model.config.decoder_start_token_id
logits = model(input_features, decoder_input_ids=decoder_input_ids).logits

print("Environment set up successful?", logits.shape[-1] == 51865)

/home/ubuntu/.local/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


Downloading:   0%|          | 0.00/1.96k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/151M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/185k [00:00<?, ?B/s]

Environment set up successful? True


In [4]:
#!pwd
#!huggingface-cli repo create whisper-small-amet
!git lfs install
!git clone https://huggingface.co/drmeeseeks/whisper-small-amet
!cd whisper-small-amet
#!cp ~/community-events/whisper-fine-tuning-event/run_speech_recognition_seq2seq_streaming.py .

Error: Failed to call git rev-parse --git-dir: exit status 128 
Git LFS initialized.
Cloning into 'whisper-small-amet'...
remote: Enumerating objects: 3, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (2/2), done.
remote: Total 3 (delta 0), reused 0 (delta 0), pack-reused 0
Unpacking objects: 100% (3/3), 409 bytes | 409.00 KiB/s, done.


In [ ]:
#!pwd
#!cp ./community-events/whisper-fine-tuning-event/run_speech_recognition_seq2seq_streaming.py .
#!ls

/content
community-events			     sample_data
run_speech_recognition_seq2seq_streaming.py  whisper-small-amet


In [23]:
!rm run.sh
!echo 'python run_speech_recognition_seq2seq_streaming.py \
          --model_name_or_path="openai/whisper-small" \
          --dataset_name="google/fleurs" \
          --dataset_config_name="am_et" \
          --language="amharic" \
          --train_split_name="train+validation" \
          --eval_split_name="test" \
          --model_index_name="Whisper Small Amharic FLEURS" \
          --max_steps="1000" \
          --output_dir="./whisper-small-amet" \
          --per_device_train_batch_size="64" \
          --per_device_eval_batch_size="32" \
          --gradient_accumulation_steps="1" \
          --logging_steps="25" \
          --learning_rate="1e-5" \
          --warmup_steps="500" \
          --evaluation_strategy="steps" \
          --eval_steps="10000" \
          --save_strategy="steps" \
          --save_steps="100" \
          --generation_max_length="225" \
          --length_column_name="input_length" \
          --max_duration_in_seconds="30" \
          --text_column_name="raw_transcription" \
          --freeze_feature_encoder="False" \
          --report_to="tensorboard" \
          --metric_for_best_model="wer" \
          --greater_is_better="False" \
          --load_best_model_at_end="False" \
          --gradient_checkpointing \
          --fp16 \
          --overwrite_output_dir \
          --do_train \
          --do_eval="False" \
          --predict_with_generate \
          --do_normalize_eval="False" \
          --use_auth_token \
          --no_streaming \
          --push_to_hub="True"' >> run.sh

In [15]:
#!bash run.sh #from terminal
#!cd whisper_small-amet
!cp ./run.sh ./whisper-small-amet
!cp ./whisper_python_am_et.ipynb ./whisper-small-amet

- V100 / 16 GB GPU --> Small Model [16,2,8] = [Train Batch Size, Gradient Acc Steps, Eval Batch Size]
- A100 / 40 GB GPU --> Small Model [64,1,32] = [Train Batch Size, Gradient Acc Steps, Eval Batch Size]

In [ ]:
!python run_eval_whisper_streaming.py --model_id="openai/whisper-small" --dataset="google/fleurs" --config="am_et" --batch_size=32 --max_eval_samples=64 --device=0 --language="am"

In [ ]:
!ls
!tar -zcvf ./whisper.tar ./whisper-small-amet

community-events  run_speech_recognition_seq2seq_streaming.py
content		  sample_data
run.sh		  whisper-small-amet
./content/whisper-small-amet/
./content/whisper-small-amet/tokenizer_config.json
./content/whisper-small-amet/.git/
./content/whisper-small-amet/.git/FETCH_HEAD
./content/whisper-small-amet/.git/index
./content/whisper-small-amet/.git/branches/
./content/whisper-small-amet/.git/hooks/
./content/whisper-small-amet/.git/hooks/prepare-commit-msg.sample
./content/whisper-small-amet/.git/hooks/post-checkout
./content/whisper-small-amet/.git/hooks/commit-msg.sample
./content/whisper-small-amet/.git/hooks/pre-commit.sample
./content/whisper-small-amet/.git/hooks/pre-push
./content/whisper-small-amet/.git/hooks/fsmonitor-watchman.sample
./content/whisper-small-amet/.git/hooks/pre-rebase.sample
./content/whisper-small-amet/.git/hooks/pre-applypatch.sample
./content/whisper-small-amet/.git/hooks/pre-receive.sample
./content/whisper-small-amet/.git/hooks/applypatch-msg.sample
./conten